In [1]:
import pandas as pd
import os
import subprocess
from Bio.PDB import PDBParser
from Bio.PDB import Model
import sys
import numpy as np
import re
from Bio.Data import IUPACData
import shutil
from pathlib import PosixPath

In [2]:
protein_letters_3to1 = {value:key for key,value in IUPACData.protein_letters_1to3.items()}
protein_letters_1to3 = {key:value for key,value in IUPACData.protein_letters_1to3.items()}

In [3]:
!pwd

/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks


In [8]:
clinvar_expanded = pd.read_pickle('/ibex/scratch/penaguka/run_pipeline/clinvar_expanded.pkl')

In [3]:
pd.set_option('display.width', None)
pd.set_option('display.max_columns', None) 

In [4]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.min_rows', 50)

In [6]:
clinvar_expanded['prot_length'].nlargest(50)

9605     8797
9606     8797
5090     8525
5091     8525
5092     8525
5093     8525
8422     6306
8423     6306
8424     6306
8425     6306
8426     6306
8427     6306
8428     6306
8429     6306
8430     6306
8733     6306
8734     6306
9316     6306
3653     5604
5045     5604
5046     5604
5047     5604
16651    5537
16652    5537
16653    5537
16654    5537
16655    5537
16656    5537
16657    5537
16658    5537
16659    5537
16660    5537
16661    5537
16662    5537
16663    5537
16664    5537
16665    5537
16666    5537
16667    5537
16668    5537
16669    5537
16670    5537
16671    5537
16672    5537
16673    5537
16674    5537
16675    5537
16676    5537
16677    5537
16678    5537
Name: prot_length, dtype: int64

In [6]:
top_rows = clinvar_expanded.nlargest(20, 'prot_length')

In [7]:
top_rows

CHR        POS       ID REF ALT AF_ESP AF_EXAC AF_TGP ALLELEID  \
9605   6  152458881  1693110   A   G    NaN     NaN    NaN  1685550   
9606   6  152510340   522970   A   T    NaN   2e-05    NaN   513567   
5090   2  151619648  1501318   G   C    NaN     NaN    NaN  1402066   
5091   2  151619648  1501318   G   C    NaN     NaN    NaN  1402066   
5092   2  151643290   570495   C   T  8e-05   1e-05      0   557617   
5093   2  151643290   570495   C   T  8e-05   1e-05      0   557617   
8422   5   90716490   802125   G   T    NaN     NaN    NaN   790567   
8423   5   90716496  1217225   G   A    NaN     NaN    NaN  1207205   
8424   5   90759569   228265   T   G    NaN     NaN    NaN   229348   
8425   5   90776560   804244   G   T    NaN     NaN    NaN   792600   
8426   5   90790948   226443   G   T    NaN     NaN    NaN   228242   
8427   5   90791346   438169   G   C    NaN     NaN    NaN   431686   
8428   5   90823596  1065038   G   C    NaN     NaN    NaN  1053247   
8429   5   90848812  1217226   C   T    NaN     NaN    NaN  1207206   
8430   5   90855791  1700143   A   G    NaN     NaN    NaN  1692538   
8733   5   90652438  1217227   A   C    NaN     NaN    NaN  1207207   
8734   5   90657917   829996   T   G    NaN     NaN    NaN   818240   
9316   5   90985501     6802   A   G    NaN     NaN    NaN    21841   
3653   2  178768724   254164   A   G    NaN     NaN    NaN   248627   
5045   2  178781157   522931   C   T    NaN     NaN    NaN   513519   

                                                 CLNDN CLNDNINCL  \
9605                       [Dilated_cardiomyopathy_1A]       NaN   
9606         [Autosomal_recessive_ataxia,_Beauce_type]       NaN   
5090                             [Nemaline_myopathy_2]       NaN   
5091                             [Nemaline_myopathy_2]       NaN   
5092                             [Nemaline_myopathy_2]       NaN   
5093                             [Nemaline_myopathy_2]       NaN   
8422                          [Usher_syndrome_type_2C]       NaN   
8423                 [Idiopathic_generalized_epilepsy]       NaN   
8424                           [Rare_genetic_deafness]       NaN   
8425               [ADGRV1-related_myoclonic_epilepsy]       NaN   
8426                           [Usher_syndrome_type_1]       NaN   
8427                                  [Usher_syndrome]       NaN   
8428                              [Hearing_impairment]       NaN   
8429                 [Idiopathic_generalized_epilepsy]       NaN   
8430                   [Febrile_seizures,_familial,_4]       NaN   
8733                 [Idiopathic_generalized_epilepsy]       NaN   
8734                          [Usher_syndrome_type_2C]       NaN   
9316                          [Usher_syndrome_type_2C]       NaN   
3653                       [Dilated_cardiomyopathy_1G]       NaN   
5045  [Early-onset_myopathy_with_fatal_cardiomyopathy]       NaN   

                                               CLNDISDB CLNDISDBINCL  \
9605  MONDO:MONDO:0007269,MedGen:C1449563,OMIM:11520...          NaN   
9606  MONDO:MONDO:0012549,MedGen:C1853116,OMIM:61074...          NaN   
5090    MONDO:MONDO:0009725,MedGen:C1850569,OMIM:256030          NaN   
5091    MONDO:MONDO:0009725,MedGen:C1850569,OMIM:256030          NaN   
5092    MONDO:MONDO:0009725,MedGen:C1850569,OMIM:256030          NaN   
5093    MONDO:MONDO:0009725,MedGen:C1850569,OMIM:256030          NaN   
8422  MONDO:MONDO:0011558,MedGen:C2931213,OMIM:60547...          NaN   
8423  MONDO:MONDO:0005579,MedGen:C0270850,OMIM:60066...          NaN   
8424                     MedGen:CN826980,Orphanet:96210          NaN   
8425                                                  .          NaN   
8426  MONDO:MONDO:0010168,MedGen:C1568247,OMIM:27690...          NaN   
8427  MONDO:MONDO:0019501,MeSH:D052245,MedGen:C02710...          NaN   
8428  Human_Phenotype_Ontology:HP:0000365,Human_Phen...          NaN   
8429  MONDO:MONDO:0005579,MedGen:C0270850,OMIM:60066...          NaN   
8430

In [15]:
clinvar_expanded['PDB_path'].loc[9605]

PosixPath('/ibex/scratch/projects/c2102/databases/alphafold/alphafold_human_v4/AF-Q8NF91-F2-model_v4.pdb')

In [16]:
for path in clinvar_expanded['PDB_path']:
    print(path)

/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P82279-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P82279-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P82279-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P82279-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P82279-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P82279-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P82279-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P82279-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P82279-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P82279-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P82279-F1-model_v4.pdb
/ibex/scra

In [9]:
clinvar_expanded

CHR        POS       ID REF ALT   AF_ESP  AF_EXAC AF_TGP ALLELEID  \
0       1  197429459  1048144   G   C      NaN      NaN    NaN  1036051   
1       1  197429466  1213987   T   G      NaN      NaN    NaN  1203980   
2       1  197429467  1963628   G   A      NaN      NaN    NaN  2017299   
3       1  197429468  2202910   G   C      NaN      NaN    NaN  1928560   
4       1  197429473   978993   G   T      NaN      NaN    NaN   967053   
...    ..        ...      ...  ..  ..      ...      ...    ...      ...   
31053   Y    2787408  1177296   C   G      NaN      NaN    NaN  1166601   
31054   Y    2787412     9747   C   T      NaN      NaN    NaN    24786   
31055   Y    2787515   492908   C   A      NaN      NaN    NaN   485861   
31056   Y    2787551     9754   C   T      NaN    9e-05    NaN    24793   
31057   Y    7063898   625467   A   T  0.00123  0.00048    NaN   613772   

                                                   CLNDN CLNDNINCL  \
0                         [Leber_congenital_amaurosis_8]       NaN   
1                              [Retinitis_pigmentosa_12]       NaN   
2      [Retinitis_pigmentosa_12, Leber_congenital_ama...       NaN   
3      [Retinitis_pigmentosa_12, Leber_congenital_ama...       NaN   
4             [Autosomal_recessive_retinitis_pigmentosa]       NaN   
...                                                  ...       ...   
31053                [46,XY_disorder_of_sex_development]       NaN   
31054                             [46,XY_sex_reversal_1]       NaN   
31055                             [46,XY_sex_reversal_1]       NaN   
31056                             [46,XY_sex_reversal_1]       NaN   
31057                             [Deafness,_Y-linked_2]       NaN   

                                                CLNDISDB CLNDISDBINCL  \
0      MONDO:MONDO:0013453,MedGen:C3151202,OMIM:61383...          NaN   
1      MONDO:MONDO:0010818,MedGen:C1838647,OMIM:60010...          NaN   
2      MONDO:MONDO:0010818,MedGen:C1838647,OMIM:60010...          NaN   
3      MONDO:MONDO:0010818,MedGen:C1838647,OMIM:60010...          NaN   
4                                        MedGen:C0339526          NaN   
...                                                  ...          ...   
31053  MONDO:MONDO:0020040,MedGen:C2751824,Orphanet:9...          NaN   
31054  MONDO:MONDO:0020712,MedGen:C2748896,OMIM:40004...          NaN   
31055  MONDO:MONDO:0020712,MedGen:C2748896,OMIM:40004...          NaN   
31056  MONDO:MONDO:0020712,MedGen:C2748896,OMIM:40004...          NaN   
31057    MONDO:MONDO:0027048,MedGen:C5193013,OMIM:400047          NaN   

                           CLNHGVS                           CLNREVSTAT  \
0      NC_000001.11:g.197429459G>C  criteria_provided,_single_submitter   
1      NC_000001.11:g.197429466T>G  criteria_provided,_single_submitter   
2      NC_000001.11:g.197429467G>A  criteria_provided,_single_submitter   
3      NC_000001.11:g.197429468G>C  criteria_provided,_single_submitter   
4      NC_000001.11:g.197429473G>T       no_assertion_criteria_provided   
...                            ...                                  ...   
31053    NC_000024.10:g.2787408C>G  criteria_provided,_single_submitter   
31054    NC_000024.10:g.2787412C>T       no_assertion_criteria_provided   
31055    NC_000024.10:g.2787515C>A       no_assertion_criteria_provided   
31056    NC_000024.10:g.2787551C>T       no_assertion_criteria_provided   
31057    NC_000024.10:g.7063898A>T       no_assertion_criteria_provided   

                  CLNSIG CLNSIGCONF CLNSIGINCL                      CLNVC  \
0      Likely_pathogenic        NaN        NaN  single_nucleotide_variant   
1      Likely_pathogenic        NaN        NaN  single_nucleotide_variant   
2      Likely_pathogenic        NaN        NaN  single_nucleotide_variant   
3             Pathogenic        NaN        NaN  single_nucleotide_variant   
4             Pathogenic        NaN        NaN  single_nucleotide_variant   
...                  ...

In [10]:
clinvar_expanded['PDB_path'].value_counts()

/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-A0A024R7D5-F1-model_v4.pdb    560
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P35498-F1-model_v4.pdb        501
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q99250-F1-model_v4.pdb        382
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P02461-F1-model_v4.pdb        380
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P08123-F1-model_v4.pdb        263
                                                                                                ... 
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_human_v4/AF-Q9Y2Y1-F1-model_v4.pdb      1
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P06681-F1-model_v4.pdb          1
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-J3KP65-F1-model_v4.pdb          1
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-O00584-F1-model_v4.pdb  

In [17]:
pdb_paths = clinvar_expanded['PDB_path'].unique()

In [18]:
len(pdb_paths)

3935

In [22]:
!ls | grep -c '\.pdb$'

23


In [10]:
# Path to the output folder
output_folder = '/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs'

In [ ]:
# Create the output folder if it doesn't exist
os.makedirs(output_folder, exist_ok=True)

for path in clinvar_expanded['PDB_path'].unique():
    path = str(path)
    file_name = path.split("/")[-1].split(".")[0]
    # Create a PDB parser object
    parser = PDBParser()

    # Parse the PDB file
    structure = parser.get_structure(file_name, path)

    # Get the sequence from the first chain in the structure
    chains = structure.get_chains()
    
    prot_dict = {}
    for chain in chains:
        chain_id = chain.get_id()
        sequence = ''.join([protein_letters_3to1[residue.get_resname().lower().capitalize()] for residue in chain])
        print(sequence)
        prot_dict[chain_id] = sequence
        
    protein_folder = os.path.join(output_folder, file_name)
    os.makedirs(protein_folder, exist_ok=True)

    # Write the sequence to the FASTA file
    fasta_file = os.path.join(protein_folder, f'{file_name}.fasta')
    with open(fasta_file, 'w') as f:
        if len(prot_dict)==1:
            f.write(f'>{structure.id}\n')
            f.write(f'{sequence}\n')
        else:
            for key in prot_dict:
                f.write(f'>{structure.id}|{key}\n')
                f.write(f'{prot_dict[key]}\n')

...
MAQPTASAQKLVRPIRAVCRILQIPESDPSNLRP
...


In [11]:
folder_path = '/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs'  # Specify the folder path

subfolders = [f for f in os.listdir(folder_path) if os.path.isdir(os.path.join(folder_path, f))]

In [12]:
len(subfolders)

3938

In [9]:
paths_list = clinvar_full['PDB_path'].unique()

In [10]:
paths = [str(x).split("/")[-1].split(".")[0] for x in paths_list]

In [11]:
paths

['AF-P82279-F1-model_v4',
 'AF-P08575-F1-model_v4',
 'AF-Q15058-F1-model_v4',
 'AF-Q5T1V6-F1-model_v4',
 'AF-Q11203-F1-model_v4',
 'AF-Q5VTB9-F1-model_v4',
 'AF-Q9NR50-F1-model_v4',
 'AF-P06132-F1-model_v4',
 'AF-Q96IR7-F1-model_v4',
 'AF-P56696-F1-model_v4',
 'AF-Q9HAB8-F1-model_v4',
 'AF-Q8N6F1-F1-model_v4',
 'AF-Q32P28-F1-model_v4',
 'AF-P11166-F1-model_v4',
 'AF-P30613-F1-model_v4',
 'AF-P14324-F1-model_v4',
 'AF-Q9NR48-F5-model_v4',
 'AF-Q9NR48-F1-model_v4',
 'AF-Q9BUK6-F1-model_v4',
 'AF-Q92963-F1-model_v4',
 'AF-A0A384MQX1-F1-model_v4',
 'AF-Q15392-F1-model_v4',
 'AF-Q5VU50-F1-model_v4',
 'AF-Q8NBP7-F1-model_v4',
 'AF-Q9H2M9-F1-model_v4',
 'AF-Q9NVF7-F1-model_v4',
 'AF-A0A024R3P1-F1-model_v4',
 'AF-A0A499FIZ0-F1-model_v4',
 'AF-Q14739-F1-model_v4',
 'AF-A1NY77-F1-model_v4',
 'AF-A0A0S2Z5U6-F1-model_v4',
 'AF-P98160-F14-model_v4',
 'AF-P98160-F5-model_v4',
 'AF-O75445-F14-model_v4',
 'AF-O75445-F13-model_v4',
 'AF-O75445-F12-model_v4',
 'AF-O75445-F10-model_v4',
 'AF-O75445-F9-mo

In [11]:
len(paths)

3935

In [218]:
with open('clinvar_raptorx.pkl', 'wb') as file:
    pickle.dump(paths, file)

In [18]:
# Obtener los elementos en lista1 pero no en lista2
diferencia1 = set(subfolders) - set(paths)

# Obtener los elementos en lista2 pero no en lista1
diferencia2 = set(paths) - set(subfolders)

# Imprimir los resultados
print("Elementos en subfolders pero no en paths:", diferencia1)
print("Elementos en paths pero no en subfolders:", diferencia2)

Elementos en subfolders pero no en paths: {'ibex_out', 'jobs', '.ipynb_checkpoints'}
Elementos en paths pero no en subfolders: set()


In [174]:
for protein_name in paths:
    protein_folder = os.path.join(output_folder, protein_name)
    fasta_path = os.path.join(protein_folder, f'{protein_name}.fasta')
    sbatch_file = os.path.join(output_folder, f'jobs/{protein_name}.sbatch')
    output_file = os.path.join(protein_folder, f'{protein_name}_PROP')
    
    with open(sbatch_file, 'w') as f:
        f.write("#!/bin/bash\n")
        f.write(f'#SBATCH -N 1\n')
        f.write(f"#SBATCH --job-name={protein_name}\n")
        f.write("#SBATCH --ntasks-per-node=1\n")
        f.write("#SBATCH --cpus-per-task=4\n")
        f.write("#SBATCH --mem=32\n")
        f.write("#SBATCH --time=12:00:00\n")
        f.write(f"#SBATCH --output=/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/ibex_out/{protein_name}.out\n")
        f.write(f"#SBATCH --error=/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/ibex_out/{protein_name}.err\n")
        f.write("#SBATCH --partition=batch\n")
        f.write(f"conda activate /ibex/scratch/penaguka/run_pipeline/variant_annotator/env\n")

        f.write("\n")
        f.write("# Run the RaptorX for each protein\n")
        f.write(f"/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/Predict_Property/Predict_Property.sh -i {fasta_path} -o {output_file}")

In [20]:
sorted_list = sorted(subfolders)

print(sorted_list)

['.ipynb_checkpoints', 'AF-A0A024QYX0-F1-model_v4', 'AF-A0A024QYX1-F1-model_v4', 'AF-A0A024QYX5-F1-model_v4', 'AF-A0A024QYX8-F1-model_v4', 'AF-A0A024QYY9-F1-model_v4', 'AF-A0A024QZ03-F1-model_v4', 'AF-A0A024QZ20-F1-model_v4', 'AF-A0A024QZ23-F1-model_v4', 'AF-A0A024QZ30-F1-model_v4', 'AF-A0A024QZ57-F1-model_v4', 'AF-A0A024QZ70-F1-model_v4', 'AF-A0A024QZ74-F1-model_v4', 'AF-A0A024QZ86-F1-model_v4', 'AF-A0A024QZA8-F1-model_v4', 'AF-A0A024QZA9-F1-model_v4', 'AF-A0A024QZB8-F1-model_v4', 'AF-A0A024QZD1-F1-model_v4', 'AF-A0A024QZE3-F1-model_v4', 'AF-A0A024QZE4-F1-model_v4', 'AF-A0A024QZF1-F1-model_v4', 'AF-A0A024QZP2-F1-model_v4', 'AF-A0A024QZQ2-F1-model_v4', 'AF-A0A024QZS1-F1-model_v4', 'AF-A0A024QZT2-F1-model_v4', 'AF-A0A024QZT7-F1-model_v4', 'AF-A0A024QZY1-F1-model_v4', 'AF-A0A024QZY7-F1-model_v4', 'AF-A0A024R040-F1-model_v4', 'AF-A0A024R050-F1-model_v4', 'AF-A0A024R064-F1-model_v4', 'AF-A0A024R068-F1-model_v4', 'AF-A0A024R089-F1-model_v4', 'AF-A0A024R0C3-F1-model_v4', 'AF-A0A024R0F8-F1-mo

In [138]:
for protein_name in rest:
    protein_folder = os.path.join(output_folder, protein_name)
    fasta_path = os.path.join(protein_folder, f'{protein_name}.fasta')
    sbatch_file = os.path.join(output_folder, f'jobs/{protein_name}.sbatch')
    output_file = os.path.join(protein_folder, f'{protein_name}_PROP')
    
    with open(sbatch_file, 'w') as f:
        f.write("#!/bin/bash\n")
        f.write(f'#SBATCH -N 1\n')
        f.write(f"#SBATCH --job-name={protein_name}\n")
        f.write("#SBATCH --ntasks-per-node=1\n")
        f.write("#SBATCH --cpus-per-task=4\n")
        f.write("#SBATCH --mem=128\n")
        f.write("#SBATCH --time=12:00:00\n")
        f.write(f"#SBATCH --output=/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/ibex_out/{protein_name}.out\n")
        f.write(f"#SBATCH --error=/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/ibex_out/{protein_name}.err\n")
        f.write("#SBATCH --partition=batch\n")
        f.write(f"conda activate /ibex/scratch/penaguka/run_pipeline/variant_annotator/env\n")

        f.write("\n")
        f.write("# Run the RaptorX for each protein\n")
        f.write(f"/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/Predict_Property/Predict_Property.sh -i {fasta_path} -o {output_file}")

In [59]:
folder_path = '/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs'

In [ ]:
'/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-P35556-F1-model_v4'

In [205]:
ss8_folders = []
for root, dirs, files in os.walk(folder_path):
    for file in files:
        file_name = file.split(".")[0]
        if file.endswith(".ss8"):
            ss8_folders.append(file_name)

In [79]:
ss8_folders

['AF-A0A0S2Z4G5-F1-model_v4',
 'AF-A0A024R189-F1-model_v4',
 'AF-A0A7P0T9D8-F1-model_v4',
 'AF-O95343-F1-model_v4',
 'AF-E5KRX5-F1-model_v4',
 'AF-P28062-F1-model_v4',
 'AF-A0A024QZA9-F1-model_v4',
 'AF-Q9Y366-F1-model_v4',
 'AF-P25189-F1-model_v4',
 'AF-Q6IBR2-F1-model_v4',
 'AF-P09486-F1-model_v4',
 'AF-P04000-F1-model_v4',
 'AF-P82930-F1-model_v4',
 'AF-P20674-F1-model_v4',
 'AF-P25705-F1-model_v4',
 'AF-A0A024R601-F1-model_v4',
 'AF-A0A024R9N2-F1-model_v4',
 'AF-A0A024R3I8-F1-model_v4',
 'AF-A4D2P1-F1-model_v4',
 'AF-E5KN15-F1-model_v4',
 'AF-P40306-F1-model_v4',
 'AF-A0A024RD41-F1-model_v4',
 'AF-P56178-F1-model_v4',
 'AF-O75477-F1-model_v4',
 'AF-P02489-F1-model_v4',
 'AF-C9JR72-F1-model_v4',
 'AF-A0A024R3V6-F1-model_v4',
 'AF-A0A140VK45-F1-model_v4',
 'AF-P37840-F1-model_v4',
 'AF-P07737-F1-model_v4',
 'AF-F1DAL1-F1-model_v4',
 'AF-O75603-F1-model_v4',
 'AF-D0PNI2-F1-model_v4',
 'AF-Q96DW6-F1-model_v4',
 'AF-O95954-F1-model_v4',
 'AF-A0A384MDT9-F1-model_v4',
 'AF-A0A0A0MT83-F1-m

In [206]:
len(ss8_folders)

3935

In [207]:
# Obtener los elementos en lista1 pero no en lista2
diferencia1 = set(ss8_folders) - set(paths)

# Obtener los elementos en lista2 pero no en lista1
diferencia2 = set(paths) - set(ss8_folders)

# Imprimir los resultados
#print("Elementos en ss8_folders pero no en paths:", diferencia1)
#print("Elementos en paths pero no en ss8_folders:", diferencia2)

In [208]:
rest = list(diferencia2)

In [74]:
rest

['AF-Q63HN8-F1-model_v4',
 'AF-Q14643-F7-model_v4',
 'AF-Q8NBH2-F1-model_v4',
 'AF-Q9UG01-F1-model_v4',
 'AF-Q6SJ93-F1-model_v4',
 'AF-O14802-F1-model_v4',
 'AF-Q86UK5-F1-model_v4',
 'AF-P00450-F1-model_v4',
 'AF-P08F94-F6-model_v4',
 'AF-A0A024R328-F1-model_v4',
 'AF-Q7Z7M0-F5-model_v4',
 'AF-A0A0A0MQU7-F1-model_v4',
 'AF-P54136-F1-model_v4',
 'AF-Q7RTU9-F1-model_v4',
 'AF-Q06787-F1-model_v4',
 'AF-Q13753-F1-model_v4',
 'AF-A0A024R854-F1-model_v4',
 'AF-P21817-F2-model_v4',
 'AF-Q9Y5B9-F1-model_v4',
 'AF-A0A7P0MRI8-F1-model_v4',
 'AF-Q9UKN7-F9-model_v4',
 'AF-Q9HCM3-F1-model_v4',
 'AF-O75762-F1-model_v4',
 'AF-Q02388-F9-model_v4',
 'AF-Q9HBA0-F1-model_v4',
 'AF-O14522-F1-model_v4',
 'AF-Q2KHM9-F1-model_v4',
 'AF-Q9Y6D9-F1-model_v4',
 'AF-O60885-F1-model_v4',
 'AF-P00734-F1-model_v4',
 'AF-A0A024R6B9-F1-model_v4',
 'AF-O75369-F1-model_v4',
 'AF-Q68DH5-F1-model_v4',
 'AF-Q96SN8-F1-model_v4',
 'AF-Q8WZ42-F3-model_v4',
 'AF-O75179-F1-model_v4',
 'AF-Q8NDL9-F1-model_v4',
 'AF-Q6ZNJ1-F8-mod

In [209]:
len(rest)

0

In [203]:
less_rest = rest[0:42]

In [85]:
less_rest

['AF-A0A024QZ70-F1-model_v4',
 'AF-Q14315-F5-model_v4',
 'AF-Q02505-F1-model_v4',
 'AF-A1PUP8-F1-model_v4',
 'AF-Q12791-F1-model_v4',
 'AF-J3KNI1-F1-model_v4',
 'AF-A0A3B3ISR2-F1-model_v4',
 'AF-Q8NET8-F1-model_v4',
 'AF-Q7Z3E5-F1-model_v4',
 'AF-P08069-F1-model_v4',
 'AF-O75112-F1-model_v4',
 'AF-Q99996-F6-model_v4',
 'AF-Q13009-F1-model_v4',
 'AF-Q9HC78-F1-model_v4',
 'AF-P98161-F3-model_v4',
 'AF-O95267-F1-model_v4',
 'AF-P40692-F1-model_v4',
 'AF-Q8NCM8-F8-model_v4',
 'AF-Q15751-F19-model_v4',
 'AF-Q14980-F1-model_v4',
 'AF-P16885-F1-model_v4',
 'AF-Q9HCE0-F1-model_v4',
 'AF-Q9UKP5-F1-model_v4',
 'AF-Q99698-F2-model_v4',
 'AF-P00747-F1-model_v4',
 'AF-Q93063-F1-model_v4',
 'AF-P27708-F1-model_v4',
 'AF-Q8IWN7-F1-model_v4',
 'AF-P49736-F1-model_v4',
 'AF-Q9UKY4-F1-model_v4',
 'AF-P78504-F1-model_v4',
 'AF-O75445-F19-model_v4',
 'AF-P78509-F10-model_v4',
 'AF-P42858-F10-model_v4',
 'AF-Q8WXX7-F1-model_v4',
 'AF-Q9ULW8-F1-model_v4',
 'AF-Q9BYN7-F1-model_v4',
 'AF-P47989-F1-model_v4',


In [28]:
import subprocess

In [204]:
for protein_name in less_rest:
    protein_folder = os.path.join(output_folder, protein_name)
    fasta_path = os.path.join(protein_folder, f'{protein_name}.fasta')
    command = f'sbatch /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/jobs/{protein_name}.sbatch'
    result = subprocess.run(command, shell=True, capture_output=True, text=True)

In [51]:
!squeue -u penaguka

             JOBID PARTITION     NAME     USER ST       TIME  NODES NODELIST(REASON)
          26078840     batch  jupyter penaguka  R    1:28:24      1 cn605-23-r


In [ ]:
['AF-A0A0S2Z4G5-F1-model_v4.seq', 'AF-A0A0S2Z4G5-F1-model_v4.summary', 'AF-A0A0S2Z4G5-F1-model_v4.tm8', 'AF-A0A0S2Z4G5-F1-model_v4.ss3_simp', 'AF-A0A0S2Z4G5-F1-model_v4.ss8_simp', 'AF-A0A0S2Z4G5-F1-model_v4.diso', 'AF-A0A0S2Z4G5-F1-model_v4.all', 'AF-A0A0S2Z4G5-F1-model_v4.fasta', 'AF-A0A0S2Z4G5-F1-model_v4.tm8_simp', 'AF-A0A0S2Z4G5-F1-model_v4.tm2', '0README_noprof', '.ss8', '.acc', '.acc_simp', '.ss3', '.diso_simp', '.tm2_simp']

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-A0A0S2Z4G5-F1-model_v4/AF-A0A0S2Z4G5-F1-model_v4.all

In [ ]:
sbatch AF-Q63HN8-F1-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q9BYI3-F1-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q7Z6Z7-F10-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q9NZW4-F1-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/jobs/AF-Q14204-F11-model_v4.sbatch

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q5VTB9-F1-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q8WZ42-F13-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q9Y2H9-F1-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q8WZ42-F1-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q8WZ42-F3-model_v4

In [ ]:
AF-Q8WZ42-F2-model_v4]$ cd /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/ibex_out/AF-Q8WZ42-F3-model_v4.err

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q14204-F11-model_v4

In [ ]:
 AF-A0A0S2Z4G5-F1-model_v4_PROP

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-A0A0S2Z4G5-F1-model_v4

In [ ]:
cd /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-P35556-F1-model_v4

In [ ]:
find /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/ -type d -name 'TMP_TGTGEN_*' -exec rm -r {} \;

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-A0A0S2Z4G5-F1-model_v4/AF-A0A0S2Z4G5-F1-model_v4_PROP/AF-A0A0S2Z4G5-F1-model_v4.all

### Add raptor x notations

In [12]:
clinvar_full = clinvar_expanded.copy()

In [13]:
clinvar_full.isnull().sum()

CHR                           0
POS                           0
ID                            0
REF                           0
ALT                           0
AF_ESP                    30696
AF_EXAC                   28797
AF_TGP                    30732
ALLELEID                      0
CLNDN                         0
CLNDNINCL                 30999
CLNDISDB                      0
CLNDISDBINCL              30999
CLNHGVS                       0
CLNREVSTAT                    0
CLNSIG                        0
CLNSIGCONF                31058
CLNSIGINCL                30999
CLNVC                         0
CLNVCSO                       0
CLNVI                     16607
DBVARID                   31058
MC                            4
ORIGIN                      204
RS                        10131
Allele                        0
Consequence                   0
IMPACT                        0
GENEID                        0
Gene                          0
Feature_type                  0
Feature 

In [14]:
clinvar_full

CHR        POS       ID REF ALT   AF_ESP  AF_EXAC AF_TGP ALLELEID  \
0       1  197429459  1048144   G   C      NaN      NaN    NaN  1036051   
1       1  197429466  1213987   T   G      NaN      NaN    NaN  1203980   
2       1  197429467  1963628   G   A      NaN      NaN    NaN  2017299   
3       1  197429468  2202910   G   C      NaN      NaN    NaN  1928560   
4       1  197429473   978993   G   T      NaN      NaN    NaN   967053   
5       1  197429555   191357   G   A      NaN      NaN    NaN   189156   
6       1  197429581   813170   G   C      NaN      NaN    NaN   801275   
7       1  197429587  1017521   T   C      NaN      NaN    NaN  1002377   
8       1  197429605  2093427   G   C      NaN      NaN    NaN  2156507   
9       1  197429614   427863   T   C      NaN      NaN    NaN   418814   
10      1  197434790  1051633   T   C      NaN      NaN    NaN  1039684   
11      1  197434877   846589   A   T      NaN    1e-05    NaN   823132   
12      1  197434880  2502418   C   A      NaN      NaN    NaN  2543901   
13      1  197434880   236473   C   T      NaN      NaN    NaN   237975   
14      1  197434937   973913   G   A      NaN      NaN    NaN   962214   
15      1  197434984   636016   A   G      NaN    1e-05    NaN   623793   
16      1  197435027   973937   T   A      NaN      NaN    NaN   962217   
17      1  197435029  2144426   G   C      NaN      NaN    NaN  1876330   
18      1  197435084  1319944   T   C      NaN      NaN    NaN  1310192   
19      1  197435171   973925   G   T      NaN      NaN    NaN   962218   
20      1  197435305  1456203   T   C      NaN      NaN    NaN  1458143   
21      1  197435323  2202913   T   A      NaN      NaN    NaN  1928563   
22      1  197435351   845976   G   T      NaN    2e-05    NaN   823134   
23      1  197435356  1067464   T   C      NaN      NaN    NaN  1054778   
24      1  197435358   978994   T   G      NaN      NaN    NaN   967054   
...    ..        ...      ...  ..  ..      ...      ...    ...      ...   
31033   X   38411953   935343   G   C      NaN      NaN    NaN   939590   
31034   X   38411955   623201   T   C      NaN      NaN    NaN   612172   
31035   X   38411956  1708452   C   T      NaN      NaN    NaN  1706750   
31036   X   38421026   870332   G   T      NaN      NaN    NaN   858497   
31037   X   38421032   870333   G   A      NaN      NaN    NaN   858498   
31038   X   38421045   859988   C   G      NaN      NaN    NaN   850038   
31039   X   38421051  2110985   A   T      NaN      NaN    NaN  2167554   
31040   X   38421056  2138547   C   T      NaN      NaN    NaN  1878242   
31041   Y    2787207     9752   G   A      NaN      NaN    NaN    24791   
31042   Y    2787224     9756   T   A      NaN      NaN    NaN    24795   
31043   Y    2787224   470196   T   C      NaN      NaN    NaN   472023   
31044   Y    2787267     9744   C   T      NaN      NaN    NaN    24783   
31045   Y    2787278     9738   A   G      NaN      NaN    NaN    24777   
31046   Y    2787287     9742   T   A      NaN      NaN    NaN    24781   
31047   Y    2787320     9755   C   T      NaN      NaN    NaN    24794   
31048   Y    2787321     9750   C   G      NaN      NaN    NaN    24789   
31049   Y    2787334     9741   G   C      NaN      NaN    NaN    24780   
31050   Y    2787377   393470   C   A      NaN      NaN    NaN   380292   
31051   Y    2787392  1470948   G   T      NaN      NaN    NaN  1395175   
31052   Y    2787401     9746   A   G      NaN      NaN    NaN    24785   
31053   Y    2787408  1177296   C   G      NaN      NaN    NaN  1166601   
31054   Y    2787412     9747   C   T      NaN      NaN    NaN    24786   
31055   Y    2787515   492908   C   A      NaN      NaN    NaN   485861   
31056   Y    2787551     9754   C   T      NaN    9e-05    NaN    24793   
31057   Y    7063898   625467   A   T  0.00123  0.00048    NaN   613772   

                                                   CLNDN CLNDNINCL  \
0                         [Leber_co

In [15]:
column_names = ['ss8_pred', 'ss8_H', 'ss8_G', 'ss8_I', 'ss8_E', 'ss8_B', 'ss8_T', 'ss8_S', 'ss8_L',
                'acc_pred', 'acc_B', 'acc_M', 'acc_E',
                'diso_pred', 'diso_score',
                'tm8_pred', 'tm8_H', 'tm8_E', 'tm8_C', 'tm8_I', 'tm8_L', 'tm8_F', 'tm8_X', 'tm8__']

# Add new columns to the dataframe with no values
clinvar_full[column_names] = pd.DataFrame(columns=column_names)

In [16]:
maxasa_dict = {
    'A': 113,
    'R': 241,
    'N': 158,
    'D': 151,
    'C': 140,
    'E': 183,
    'Q': 189,
    'G': 85,
    'H': 194,
    'I': 182,
    'L': 180,
    'K': 211,
    'M': 204,
    'F': 218,
    'P': 143,
    'S': 122,
    'T': 146,
    'W': 259,
    'Y': 229,
    'V': 160
}

In [46]:
def assign_access_letter(access):
    if access <= 36:
        return 'B'
    elif access <= 71:
        return 'M'
    else:
        return 'E'

In [18]:
def assign_acc(access):
    if access <= 12:
        return 'B'
    elif access <= 42:
        return 'M'
    else:
        return 'E'

In [19]:
def retrieve_data(df,index,pos,aa):
    if (temp_df['position'].iloc[pos-1] == pos) & (temp_df['AA'].iloc[pos-1] == aa):
        for column in column_names:
            df.at[index, column] = temp_df[column].iloc[pos-1]

In [20]:
def get_raptorx(file_path):
    
    # Read the file
    with open(file_path, 'r') as file:
        file_content = file.read()
        
    # Extract SS8 predictions
    ss8_start = file_content.find('#---------------- details of SS8 prediction ---------------------------')
    ss8_end = file_content.find('#---------------- details of ACC prediction ---------------------------')
    ss8_lines = file_content[ss8_start: ss8_end]  
    #print(ss8_lines)
    # Extract ACC predictions
    acc_start = file_content.find('#---------------- details of ACC prediction ---------------------------')
    acc_end = file_content.find('#---------------- details of DISO prediction --------------------------')
    acc_lines = file_content[acc_start: acc_end]
    # Extract DISO predictions
    diso_start = file_content.find('#---------------- details of DISO prediction --------------------------')
    diso_end = file_content.find('#---------------- details of TM2 prediction ---------------------------')
    diso_lines = file_content[diso_start: diso_end]
    # Extract TM8 predictions
    tm8_start = file_content.find('#---------------- details of TM8 prediction ---------------------------')
    tm8_end = len(file_content)
    tm8_lines = file_content[tm8_start:tm8_end]
        
    # Create a ss8 DataFrame from the lines
    ss8_columns = ['position', 'AA','ss8_pred','ss8_H','ss8_G','ss8_I','ss8_E','ss8_B','ss8_T','ss8_S','ss8_L']
    ss8_rows = [line.strip() for line in ss8_lines.split('\n') if not line.startswith('#')]
    ss8_values = [row.split() for row in ss8_rows]
    data_ss8 = pd.DataFrame(ss8_values, columns=ss8_columns)
    data_ss8.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = ss8_columns[3:]
    pos_column = ss8_columns[0]
    data_ss8[numeric_columns] = data_ss8[numeric_columns].astype(float)
    data_ss8[pos_column] = data_ss8[pos_column].astype(int)
    
    # Create an acc DataFrame from the lines
    acc_columns = ['position', 'AA','acc_pred','acc_B','acc_M','acc_E']
    acc_rows = [line.strip() for line in acc_lines.split('\n') if not line.startswith('#')]
    acc_values = [row.split() for row in acc_rows]
    data_acc = pd.DataFrame(acc_values, columns=acc_columns)
    data_acc.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = acc_columns[3:]
    pos_column = acc_columns[0]
    data_acc[numeric_columns] = data_acc[numeric_columns].astype(float)
    data_acc[pos_column] = data_acc[pos_column].astype(int)
    
    # Create an diso DataFrame from the lines
    diso_columns = ['position', 'AA','diso_pred','diso_score']
    diso_rows = [line.strip() for line in diso_lines.split('\n') if not line.startswith('#')]
    diso_values = [row.split() for row in diso_rows]
    data_diso = pd.DataFrame(diso_values, columns=diso_columns)
    data_diso.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = diso_columns[3:]
    pos_column = diso_columns[0]
    data_diso[numeric_columns] = data_diso[numeric_columns].astype(float)
    data_diso[pos_column] = data_diso[pos_column].astype(int)
    
    # Create an acc DataFrame from the lines
    tm8_columns = ['position', 'AA','tm8_pred','tm8_H','tm8_E','tm8_C','tm8_I','tm8_L','tm8_F','tm8_X','tm8__']
    tm8_rows = [line.strip() for line in tm8_lines.split('\n') if not line.startswith('#')]
    tm8_values = [row.split() for row in tm8_rows]
    data_tm8 = pd.DataFrame(tm8_values, columns=tm8_columns)
    data_tm8.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = tm8_columns[3:]
    pos_column = tm8_columns[0]
    data_tm8[numeric_columns] = data_tm8[numeric_columns].astype(float)
    data_tm8[pos_column] = data_tm8[pos_column].astype(int)

    # Optionally, you can set column names
    big_df = pd.DataFrame()
    if all(df['position'].equals(data_ss8['position']) and df['AA'].equals(data_ss8['AA']) for df in [data_acc, data_diso, data_tm8]):
        # If the columns are equal, keep only one copy at the beginning of big_df
        big_df = pd.concat([data_ss8, data_acc.iloc[:, 2:], data_diso.iloc[:, 2:], data_tm8.iloc[:, 2:]], axis=1)
    else:
        # If the columns are not equal, concatenate all dataframes as usual
        print(f'Positions and AAs do not match between data_ss8, data_acc, data_diso, data_tm8 of {file_path}.')
        big_df = pd.concat([data_ss8, data_acc, data_diso, data_tm8], axis=1)
        
    #column_names = ['position', 'AA','ss_H','ss_G','ss_I','ss_E','ss_B','ss_T','ss_S','ss_L','acc_B','acc_M','acc_E','diso_score','tm8_H','tm8_E','tm8_C','tm8_I','tm8_L','tm8_F','tm8_X','tm8__']  # Replace with your actual column names
    #big_df.columns = column_names

    # Create a DataFrame from the extracted data
    return big_df

In [21]:
for item in clinvar_full['PDB_path'].unique():
    path = item
    protein = str(path).split("/")[-1].split(".")[0]
    if protein in paths:
        raptorx_preds = f'/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/{protein}/{protein}_PROP/{protein}.all'
    else:
        print(f'No RaptorX output for {protein}')
    temp_df = get_raptorx(raptorx_preds)
    for index, row in clinvar_full[clinvar_full['PDB_path'] == path].iterrows():
        #print(index)
        # Access the row data using row['column_name'] or row[column_index]
        # modify the row values directly
        # For example, update a specific column value
        pos = clinvar_full['Residue_position'].iloc[index]
        aa = protein_letters_3to1[clinvar_full['WT'].iloc[index]]
        match = re.search(r'-F(-?\d+)-', protein)
        if match:
            number = int(match.group(1))
            if number == 1:
                retrieve_data(clinvar_full,index,pos,aa)
            else:
                temp_pos = pos-((number-1)*200)
                retrieve_data(clinvar_full,index,temp_pos,aa)
        else:
            print(f"No number found for {protein}.")

In [22]:
clinvar_full

CHR        POS       ID REF ALT   AF_ESP  AF_EXAC AF_TGP ALLELEID  \
0       1  197429459  1048144   G   C      NaN      NaN    NaN  1036051   
1       1  197429466  1213987   T   G      NaN      NaN    NaN  1203980   
2       1  197429467  1963628   G   A      NaN      NaN    NaN  2017299   
3       1  197429468  2202910   G   C      NaN      NaN    NaN  1928560   
4       1  197429473   978993   G   T      NaN      NaN    NaN   967053   
5       1  197429555   191357   G   A      NaN      NaN    NaN   189156   
6       1  197429581   813170   G   C      NaN      NaN    NaN   801275   
7       1  197429587  1017521   T   C      NaN      NaN    NaN  1002377   
8       1  197429605  2093427   G   C      NaN      NaN    NaN  2156507   
9       1  197429614   427863   T   C      NaN      NaN    NaN   418814   
10      1  197434790  1051633   T   C      NaN      NaN    NaN  1039684   
11      1  197434877   846589   A   T      NaN    1e-05    NaN   823132   
12      1  197434880  2502418   C   A      NaN      NaN    NaN  2543901   
13      1  197434880   236473   C   T      NaN      NaN    NaN   237975   
14      1  197434937   973913   G   A      NaN      NaN    NaN   962214   
15      1  197434984   636016   A   G      NaN    1e-05    NaN   623793   
16      1  197435027   973937   T   A      NaN      NaN    NaN   962217   
17      1  197435029  2144426   G   C      NaN      NaN    NaN  1876330   
18      1  197435084  1319944   T   C      NaN      NaN    NaN  1310192   
19      1  197435171   973925   G   T      NaN      NaN    NaN   962218   
20      1  197435305  1456203   T   C      NaN      NaN    NaN  1458143   
21      1  197435323  2202913   T   A      NaN      NaN    NaN  1928563   
22      1  197435351   845976   G   T      NaN    2e-05    NaN   823134   
23      1  197435356  1067464   T   C      NaN      NaN    NaN  1054778   
24      1  197435358   978994   T   G      NaN      NaN    NaN   967054   
...    ..        ...      ...  ..  ..      ...      ...    ...      ...   
31033   X   38411953   935343   G   C      NaN      NaN    NaN   939590   
31034   X   38411955   623201   T   C      NaN      NaN    NaN   612172   
31035   X   38411956  1708452   C   T      NaN      NaN    NaN  1706750   
31036   X   38421026   870332   G   T      NaN      NaN    NaN   858497   
31037   X   38421032   870333   G   A      NaN      NaN    NaN   858498   
31038   X   38421045   859988   C   G      NaN      NaN    NaN   850038   
31039   X   38421051  2110985   A   T      NaN      NaN    NaN  2167554   
31040   X   38421056  2138547   C   T      NaN      NaN    NaN  1878242   
31041   Y    2787207     9752   G   A      NaN      NaN    NaN    24791   
31042   Y    2787224     9756   T   A      NaN      NaN    NaN    24795   
31043   Y    2787224   470196   T   C      NaN      NaN    NaN   472023   
31044   Y    2787267     9744   C   T      NaN      NaN    NaN    24783   
31045   Y    2787278     9738   A   G      NaN      NaN    NaN    24777   
31046   Y    2787287     9742   T   A      NaN      NaN    NaN    24781   
31047   Y    2787320     9755   C   T      NaN      NaN    NaN    24794   
31048   Y    2787321     9750   C   G      NaN      NaN    NaN    24789   
31049   Y    2787334     9741   G   C      NaN      NaN    NaN    24780   
31050   Y    2787377   393470   C   A      NaN      NaN    NaN   380292   
31051   Y    2787392  1470948   G   T      NaN      NaN    NaN  1395175   
31052   Y    2787401     9746   A   G      NaN      NaN    NaN    24785   
31053   Y    2787408  1177296   C   G      NaN      NaN    NaN  1166601   
31054   Y    2787412     9747   C   T      NaN      NaN    NaN    24786   
31055   Y    2787515   492908   C   A      NaN      NaN    NaN   485861   
31056   Y    2787551     9754   C   T      NaN    9e-05    NaN    24793   
31057   Y    7063898   625467   A   T  0.00123  0.00048    NaN   613772   

                                                   CLNDN CLNDNINCL  \
0                         [Leber_co

In [23]:
clinvar_full.isnull().sum()

CHR                           0
POS                           0
ID                            0
REF                           0
ALT                           0
AF_ESP                    30696
AF_EXAC                   28797
AF_TGP                    30732
ALLELEID                      0
CLNDN                         0
CLNDNINCL                 30999
CLNDISDB                      0
CLNDISDBINCL              30999
CLNHGVS                       0
CLNREVSTAT                    0
CLNSIG                        0
CLNSIGCONF                31058
CLNSIGINCL                30999
CLNVC                         0
CLNVCSO                       0
CLNVI                     16607
DBVARID                   31058
MC                            4
ORIGIN                      204
RS                        10131
Allele                        0
Consequence                   0
IMPACT                        0
GENEID                        0
Gene                          0
Feature_type                  0
Feature 

In [24]:
clinvar_full['tm8_pred'].value_counts()

_    24269
H     3083
X     2927
E      779
Name: tm8_pred, dtype: int64

In [47]:
clinvar_full['acc_DSSP'] = clinvar_full['accessibility'].apply(assign_access_letter)

In [26]:
clinvar_full['WT'] = clinvar_full['WT'].map(protein_letters_3to1)

In [27]:
clinvar_full['MUT'] = clinvar_full['MUT'].map(protein_letters_3to1)

In [28]:
clinvar_full['RSA'] = (clinvar_full['accessibility'] / (clinvar_full['WT'].map(maxasa_dict)))*100

In [29]:
clinvar_full['acc_RSA'] = clinvar_full['RSA'].apply(assign_acc)

In [48]:
clinvar_full['acc_match'] = np.where((clinvar_full['acc_DSSP'] == clinvar_full['acc_pred'])
                                        & (~clinvar_full['acc_DSSP'].isnull())
                                        & (~clinvar_full['acc_pred'].isnull()), 1,
                                        np.where(clinvar_full['acc_DSSP'].isnull()
                                                 | clinvar_full['acc_pred'].isnull(), np.nan, 0))

In [38]:
clinvar_full['acc_match_RSA'] = np.where((clinvar_full['acc_RSA'] == clinvar_full['acc_pred'])
                                        & (~clinvar_full['acc_RSA'].isnull())
                                        & (~clinvar_full['acc_pred'].isnull()), 1,
                                        np.where(clinvar_full['acc_RSA'].isnull()
                                                 | clinvar_full['acc_pred'].isnull(), np.nan, 0))

In [49]:
clinvar_full[['acc_DSSP','acc_pred','acc_match','acc_RSA','acc_match_RSA','acc_B','acc_M','acc_E','accessibility']]

acc_DSSP acc_pred  acc_match acc_RSA  acc_match_RSA  acc_B  acc_M  \
0            B        M        0.0       M            1.0  0.363  0.405   
1            E        E        1.0       E            1.0  0.166  0.312   
2            M        E        0.0       E            1.0  0.202  0.244   
3            M        E        0.0       E            1.0  0.202  0.244   
4            E        E        1.0       E            1.0  0.275  0.326   
5            B        B        1.0       M            0.0  0.524  0.364   
6            B        E        0.0       M            0.0  0.256  0.332   
7            B        B        1.0       M            0.0  0.556  0.362   
8            B        B        1.0       B            1.0  0.402  0.263   
9            B        B        1.0       B            1.0  0.562  0.343   
10           B        B        1.0       B            1.0  0.613   0.29   
11           E        E        1.0       E            1.0  0.175  0.397   
12           B        B        1.0       M            0.0  0.562   0.26   
13           B        B        1.0       M            0.0  0.562   0.26   
14           B        M        0.0       B            0.0  0.383  0.415   
15           B        B        1.0       B            1.0  0.577  0.322   
16           B        B        1.0       B            1.0  0.572  0.329   
17           M        M        1.0       M            1.0  0.158  0.482   
18           B        B        1.0       B            1.0  0.617  0.309   
19           B        B        1.0       M            0.0  0.486  0.326   
20           B        M        0.0       B            0.0  0.319  0.423   
21           B        B        1.0       M            0.0  0.517  0.394   
22           B        B        1.0       B            1.0  0.592  0.313   
23           M        B        0.0       M            0.0  0.507   0.37   
24           M        B        0.0       M            0.0  0.507   0.37   
...        ...      ...        ...     ...            ...    ...    ...   
31033        E        M        0.0       M            1.0  0.187  0.412   
31034        B        B        1.0       M            0.0  0.372  0.328   
31035        B        B        1.0       M            0.0  0.372  0.328   
31036        B        B        1.0       B            1.0  0.763  0.171   
31037        B        B        1.0       B            1.0  0.636  0.274   
31038        B        M        0.0       M            1.0  0.282  0.391   
31039        B        M        0.0       M            1.0  0.375  0.396   
31040        B        E        0.0       B            0.0  0.055  0.161   
31041        E        E        1.0       E            1.0  0.066  0.196   
31042        E        M        0.0       M            1.0  0.343    0.4   
31043        E        M        0.0       M            1.0  0.343    0.4   
31044        B        B        1.0       B            1.0  0.883  0.091   
31045        M        B        0.0       M            0.0  0.582  0.354   
31046        M        E        0.0       M            0.0  0.086  0.333   
31047        B        E        0.0       M            0.0   0.28  0.257   
31048        B        E        0.0       M            0.0   0.28  0.257   
31049        B        B        1.0       B            1.0    0.6  0.283   
31050        E        E        1.0       E            1.0  0.113  0.332   
31051        B        B        1.0       B            1.0  0.577  0.357   
31052        E        B        0.0       M            0.0  0.778  0.171   
31053        B        B        1.0       B            1.0   0.69   0.25   
31054        M        B        0.0       M            0.0  0.507  0.318   
31055        E        E        1.0       E            1.0  0.088  0.347   
31056        E        M        0.0       E            0.0  0.229  0.437   
31057        E        E        1.0       E            1.0  0.013  0.106   

       acc_E  accessibility  
0      0.232             23  
1      0.523             91  
2      0.554   

In [50]:
clinvar_full['acc_match'].value_counts()

1.0    16074
0.0    14984
Name: acc_match, dtype: int64

In [51]:
clinvar_full['acc_match_RSA'].value_counts()

1.0    16557
0.0    14501
Name: acc_match_RSA, dtype: int64

In [52]:
clinvar_full['ss_match'] = np.where((clinvar_full['secondary_structure'] == clinvar_full['ss8_pred'])
                                        & (~clinvar_full['secondary_structure'].isnull())
                                        & (~clinvar_full['ss8_pred'].isnull()), 1,
                                        np.where(clinvar_full['secondary_structure'].isnull()
                                                 | clinvar_full['ss8_pred'].isnull(), np.nan, 0))

In [53]:
clinvar_full['ss_match'] = clinvar_full['ss_match'].astype('Int64')

In [54]:
clinvar_full['ss_match'].isnull().sum()

7425

In [55]:
clinvar_full['ss_match'].value_counts()

1    14084
0     9549
Name: ss_match, dtype: Int64

In [56]:
clinvar_full[['secondary_structure','ss8_pred','ss_match','prot_length']]

secondary_structure ss8_pred  ss_match  prot_length
0                     NaN        T      <NA>         1406
1                       T        T         1         1406
2                       T        S         0         1406
3                       T        S         0         1406
4                       E        L         0         1406
5                       G        E         0         1406
6                     NaN        T      <NA>         1406
7                       E        L         0         1406
8                       E        T         0         1406
9                       E        E         1         1406
10                      E        E         1         1406
11                      T        T         1         1406
12                      T        T         1         1406
13                      T        T         1         1406
14                    NaN        E      <NA>         1406
15                      E        E         1         1406
16                      E        E         1         1406
17                      T        L         0         1406
18                      G        E         0         1406
19                      T        T         1         1406
20                    NaN        L      <NA>         1406
21                      E        L         0         1406
22                      E        E         1         1406
23                    NaN        L      <NA>         1406
24                    NaN        L      <NA>         1406
...                   ...      ...       ...          ...
31033                   T        G         0          354
31034                   B        G         0          354
31035                   B        G         0          354
31036                   H        H         1          354
31037                   H        H         1          354
31038                 NaN        H      <NA>          354
31039                 NaN        L      <NA>          354
31040                 NaN        L      <NA>          354
31041                 NaN        L      <NA>          204
31042                 NaN        L      <NA>          204
31043                 NaN        L      <NA>          204
31044                   H        H         1          204
31045                   H        H         1          204
31046                   H        T         0          204
31047                   H        H         1          204
31048                   H        H         1          204
31049                   H        H         1          204
31050                   H        H         1          204
31051                   H        L         0          204
31052                   H        E         0          204
31053                   H        E         0          204
31054                 NaN        E      <NA>          204
31055                 NaN        H      <NA>          204
31056                 NaN        L      <NA>          204
31057                   T        T         1          522

[31058 rows x 4 columns]

In [41]:
clinvar_full.to_pickle('clinvar_full.pkl')

In [65]:
top_rows = clinvar_full.nlargest(50, 'prot_length')

In [60]:
top_rows[['secondary_structure','ss8_pred','ss_match', 'prot_length']]

secondary_structure ss8_pred  ss_match  prot_length
9605                    H        L         0         8797
9606                    G        L         0         8797
5090                    H        H         1         8525
5091                    H        H         1         8525
5092                    H        H         1         8525
5093                    H        H         1         8525
8422                  NaN        T      <NA>         6306
8423                  NaN        S      <NA>         6306
8424                    E        E         1         6306
8425                    S        T         0         6306
8426                    T        T         1         6306
8427                    T        E         0         6306
8428                  NaN        S      <NA>         6306
8429                  NaN        L      <NA>         6306
8430                    E        H         0         6306
8733                    S        E         0         6306
8734                    E        E         1         6306
9316                    S        H         0         6306
3653                    E        E         1         5604
5045                    E        S         0         5604
5046                    E        E         1         5604
5047                  NaN        L      <NA>         5604
16651                   G        E         0         5537
16652                   G        E         0         5537
16653                   E        H         0         5537
...                   ...      ...       ...          ...
23924                   H        H         1         3530
23925                   T        H         0         3530
23926                 NaN        T      <NA>         3530
23927                   S        T         0         3530
23928                   S        T         0         3530
23929                   E        E         1         3530
23930                   H        H         1         3530
23931                   H        H         1         3530
23932                   H        H         1         3530
23933                   S        S         1         3530
23934                 NaN        L      <NA>         3530
23935                   H        H         1         3530
23936                   H        H         1         3530
23937                   H        H         1         3530
23938                   H        H         1         3530
23939                 NaN        L      <NA>         3530
23940                   T        H         0         3530
23941                 NaN        T      <NA>         3530
23942                   H        H         1         3530
23943                   H        H         1         3530
23944                   E        H         0         3530
23945                   E        H         0         3530
23946                   E        H         0         3530
23947                   E        T         0         3530
23948                   T        S         0         3530

[1000 rows x 4 columns]

In [66]:
top_rows['ss_match'].value_counts()

1    21
0    18
Name: ss_match, dtype: Int64

In [67]:
top_rows['acc_match_RSA'].value_counts()

1.0    34
0.0    16
Name: acc_match_RSA, dtype: int64

In [4]:
clinvar_full = pd.read_pickle('clinvar_full.pkl')

In [5]:
clinvar_full['secondary_structure'] = clinvar_full['secondary_structure'].fillna('L')

In [6]:
clinvar_full['ss_match'] = np.where((clinvar_full['secondary_structure'] == clinvar_full['ss8_pred'])
                                        & (~clinvar_full['secondary_structure'].isnull())
                                        & (~clinvar_full['ss8_pred'].isnull()), 1,
                                        np.where(clinvar_full['secondary_structure'].isnull()
                                                 | clinvar_full['ss8_pred'].isnull(), np.nan, 0))

In [7]:
clinvar_full['ss_match'] = clinvar_full['ss_match'].astype('Int64')

In [8]:
clinvar_full['ss_match'].isnull().sum()

0

In [9]:
clinvar_full['ss_match'].value_counts()

1    18684
0    12374
Name: ss_match, dtype: Int64

In [13]:
clinvar_full[['secondary_structure','ss8_pred','ss_match','prot_length']]

secondary_structure ss8_pred  ss_match  prot_length
0                       L        T         0         1406
1                       T        T         1         1406
2                       T        S         0         1406
3                       T        S         0         1406
4                       E        L         0         1406
5                       G        E         0         1406
6                       L        T         0         1406
7                       E        L         0         1406
8                       E        T         0         1406
9                       E        E         1         1406
10                      E        E         1         1406
11                      T        T         1         1406
12                      T        T         1         1406
13                      T        T         1         1406
14                      L        E         0         1406
15                      E        E         1         1406
16                      E        E         1         1406
17                      T        L         0         1406
18                      G        E         0         1406
19                      T        T         1         1406
20                      L        L         1         1406
21                      E        L         0         1406
22                      E        E         1         1406
23                      L        L         1         1406
24                      L        L         1         1406
...                   ...      ...       ...          ...
31033                   T        G         0          354
31034                   B        G         0          354
31035                   B        G         0          354
31036                   H        H         1          354
31037                   H        H         1          354
31038                   L        H         0          354
31039                   L        L         1          354
31040                   L        L         1          354
31041                   L        L         1          204
31042                   L        L         1          204
31043                   L        L         1          204
31044                   H        H         1          204
31045                   H        H         1          204
31046                   H        T         0          204
31047                   H        H         1          204
31048                   H        H         1          204
31049                   H        H         1          204
31050                   H        H         1          204
31051                   H        L         0          204
31052                   H        E         0          204
31053                   H        E         0          204
31054                   L        E         0          204
31055                   L        H         0          204
31056                   L        L         1          204
31057                   T        T         1          522

[31058 rows x 4 columns]

In [31]:
clinvar_ss_counts_1 = clinvar_full.loc[(clinvar_full['secondary_structure'] == clinvar_full['ss8_pred']) & (clinvar_full['ss_match'] == 1)].groupby(['secondary_structure', 'ss8_pred']).size().to_dict()

In [32]:
clinvar_ss_counts_1

{('E', 'E'): 3702,
 ('G', 'G'): 37,
 ('H', 'H'): 9378,
 ('L', 'L'): 4600,
 ('S', 'S'): 171,
 ('T', 'T'): 796}

In [33]:
clinvar_ss_counts_0 = clinvar_full.loc[(clinvar_full['secondary_structure'] != clinvar_full['ss8_pred']) & (clinvar_full['ss_match'] == 0)].groupby(['secondary_structure', 'ss8_pred']).size().to_dict()

In [34]:
clinvar_ss_counts_0

{('B', 'E'): 69,
 ('B', 'G'): 3,
 ('B', 'H'): 76,
 ('B', 'L'): 106,
 ('B', 'S'): 6,
 ('B', 'T'): 24,
 ('E', 'G'): 12,
 ('E', 'H'): 843,
 ('E', 'L'): 978,
 ('E', 'S'): 55,
 ('E', 'T'): 225,
 ('G', 'E'): 129,
 ('G', 'H'): 453,
 ('G', 'L'): 281,
 ('G', 'S'): 17,
 ('G', 'T'): 89,
 ('H', 'E'): 683,
 ('H', 'G'): 20,
 ('H', 'L'): 726,
 ('H', 'S'): 37,
 ('H', 'T'): 304,
 ('I', 'E'): 30,
 ('I', 'H'): 188,
 ('I', 'L'): 31,
 ('I', 'S'): 1,
 ('I', 'T'): 11,
 ('L', 'E'): 1095,
 ('L', 'G'): 21,
 ('L', 'H'): 1104,
 ('L', 'S'): 119,
 ('L', 'T'): 486,
 ('S', 'E'): 396,
 ('S', 'G'): 13,
 ('S', 'H'): 448,
 ('S', 'L'): 999,
 ('S', 'T'): 317,
 ('T', 'E'): 371,
 ('T', 'G'): 33,
 ('T', 'H'): 746,
 ('T', 'L'): 743,
 ('T', 'S'): 86}

In [36]:

clinvar_acc_counts_1 = clinvar_full.loc[(clinvar_full['acc_DSSP'] == clinvar_full['acc_pred']) & (clinvar_full['acc_match'] == 1)].groupby(['acc_DSSP', 'acc_pred']).size().to_dict()
clinvar_acc_counts_0 = clinvar_full.loc[(clinvar_full['acc_DSSP'] != clinvar_full['acc_pred']) & (clinvar_full['acc_match'] == 0)].groupby(['acc_DSSP', 'acc_pred']).size().to_dict()

clinvar_acc2_counts_1 = clinvar_full.loc[(clinvar_full['acc_RSA'] == clinvar_full['acc_pred']) & (clinvar_full['acc_match_RSA'] == 1)].groupby(['acc_RSA', 'acc_pred']).size().to_dict()
clinvar_acc2_counts_0 = clinvar_full.loc[(clinvar_full['acc_RSA'] != clinvar_full['acc_pred']) & (clinvar_full['acc_match_RSA'] == 0)].groupby(['acc_RSA', 'acc_pred']).size().to_dict()


In [37]:
clinvar_acc_counts_1

{('B', 'B'): 10608, ('E', 'E'): 3942, ('M', 'M'): 1524}

In [38]:
clinvar_acc_counts_0

{('B', 'E'): 3524,
 ('B', 'M'): 4148,
 ('E', 'B'): 1200,
 ('E', 'M'): 1888,
 ('M', 'B'): 1680,
 ('M', 'E'): 2544}

In [39]:
clinvar_acc2_counts_1

{('B', 'B'): 8770, ('E', 'E'): 5040, ('M', 'M'): 2747}

In [40]:
clinvar_acc2_counts_0

{('B', 'E'): 2395,
 ('B', 'M'): 3193,
 ('E', 'B'): 1440,
 ('E', 'M'): 1620,
 ('M', 'B'): 3278,
 ('M', 'E'): 2575}

### add ss3 raptorXpredictions

In [5]:
clinvar_full = pd.read_pickle('clinvar_full.pkl')

In [16]:
clinvar_full

CHR        POS       ID REF ALT   AF_ESP  AF_EXAC AF_TGP ALLELEID  \
0       1  197429459  1048144   G   C      NaN      NaN    NaN  1036051   
1       1  197429466  1213987   T   G      NaN      NaN    NaN  1203980   
2       1  197429467  1963628   G   A      NaN      NaN    NaN  2017299   
3       1  197429468  2202910   G   C      NaN      NaN    NaN  1928560   
4       1  197429473   978993   G   T      NaN      NaN    NaN   967053   
5       1  197429555   191357   G   A      NaN      NaN    NaN   189156   
6       1  197429581   813170   G   C      NaN      NaN    NaN   801275   
7       1  197429587  1017521   T   C      NaN      NaN    NaN  1002377   
8       1  197429605  2093427   G   C      NaN      NaN    NaN  2156507   
9       1  197429614   427863   T   C      NaN      NaN    NaN   418814   
10      1  197434790  1051633   T   C      NaN      NaN    NaN  1039684   
11      1  197434877   846589   A   T      NaN    1e-05    NaN   823132   
12      1  197434880  2502418   C   A      NaN      NaN    NaN  2543901   
13      1  197434880   236473   C   T      NaN      NaN    NaN   237975   
14      1  197434937   973913   G   A      NaN      NaN    NaN   962214   
15      1  197434984   636016   A   G      NaN    1e-05    NaN   623793   
16      1  197435027   973937   T   A      NaN      NaN    NaN   962217   
17      1  197435029  2144426   G   C      NaN      NaN    NaN  1876330   
18      1  197435084  1319944   T   C      NaN      NaN    NaN  1310192   
19      1  197435171   973925   G   T      NaN      NaN    NaN   962218   
20      1  197435305  1456203   T   C      NaN      NaN    NaN  1458143   
21      1  197435323  2202913   T   A      NaN      NaN    NaN  1928563   
22      1  197435351   845976   G   T      NaN    2e-05    NaN   823134   
23      1  197435356  1067464   T   C      NaN      NaN    NaN  1054778   
24      1  197435358   978994   T   G      NaN      NaN    NaN   967054   
...    ..        ...      ...  ..  ..      ...      ...    ...      ...   
31033   X   38411953   935343   G   C      NaN      NaN    NaN   939590   
31034   X   38411955   623201   T   C      NaN      NaN    NaN   612172   
31035   X   38411956  1708452   C   T      NaN      NaN    NaN  1706750   
31036   X   38421026   870332   G   T      NaN      NaN    NaN   858497   
31037   X   38421032   870333   G   A      NaN      NaN    NaN   858498   
31038   X   38421045   859988   C   G      NaN      NaN    NaN   850038   
31039   X   38421051  2110985   A   T      NaN      NaN    NaN  2167554   
31040   X   38421056  2138547   C   T      NaN      NaN    NaN  1878242   
31041   Y    2787207     9752   G   A      NaN      NaN    NaN    24791   
31042   Y    2787224     9756   T   A      NaN      NaN    NaN    24795   
31043   Y    2787224   470196   T   C      NaN      NaN    NaN   472023   
31044   Y    2787267     9744   C   T      NaN      NaN    NaN    24783   
31045   Y    2787278     9738   A   G      NaN      NaN    NaN    24777   
31046   Y    2787287     9742   T   A      NaN      NaN    NaN    24781   
31047   Y    2787320     9755   C   T      NaN      NaN    NaN    24794   
31048   Y    2787321     9750   C   G      NaN      NaN    NaN    24789   
31049   Y    2787334     9741   G   C      NaN      NaN    NaN    24780   
31050   Y    2787377   393470   C   A      NaN      NaN    NaN   380292   
31051   Y    2787392  1470948   G   T      NaN      NaN    NaN  1395175   
31052   Y    2787401     9746   A   G      NaN      NaN    NaN    24785   
31053   Y    2787408  1177296   C   G      NaN      NaN    NaN  1166601   
31054   Y    2787412     9747   C   T      NaN      NaN    NaN    24786   
31055   Y    2787515   492908   C   A      NaN      NaN    NaN   485861   
31056   Y    2787551     9754   C   T      NaN    9e-05    NaN    24793   
31057   Y    7063898   625467   A   T  0.00123  0.00048    NaN   613772   

                                                   CLNDN CLNDNINCL  \
0                         [Leber_co

In [14]:
column_names = ['ss3_pred','ss3_H','ss3_E','ss3_C']

In [15]:
# Add new columns to the dataframe with no values
clinvar_full[column_names] = pd.DataFrame(columns=column_names)

In [17]:
def retrieve_data(df,index,pos,aa):
    if (temp_df['position'].iloc[pos-1] == pos) & (temp_df['AA'].iloc[pos-1] == aa):
        for column in column_names:
            df.at[index, column] = temp_df[column].iloc[pos-1]

In [18]:
def get_ss3(file_path):
    
    # Read the file
    with open(file_path, 'r') as file:
        file_content = file.read()
        
    # Extract SS3 predictions
    ss3_start = file_content.find('#---------------- details of SS3 prediction ---------------------------')
    ss3_end = file_content.find('#---------------- details of SS8 prediction ---------------------------')
    ss3_lines = file_content[ss3_start: ss3_end]  
    #print(ss8_lines)
    
        
    # Create a ss8 DataFrame from the lines
    ss3_columns = ['position', 'AA','ss3_pred','ss3_H','ss3_E','ss3_C']
    ss3_rows = [line.strip() for line in ss3_lines.split('\n') if not line.startswith('#')]
    ss3_values = [row.split() for row in ss3_rows]
    data_ss3 = pd.DataFrame(ss3_values, columns=ss3_columns)
    data_ss3.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = ss3_columns[3:]
    pos_column = ss3_columns[0]
    data_ss3[numeric_columns] = data_ss3[numeric_columns].astype(float)
    data_ss3[pos_column] = data_ss3[pos_column].astype(int)

    # Optionally, you can set column names
    big_df = pd.DataFrame()
    big_df = data_ss3
        
    #column_names = ['position', 'AA','ss_H','ss_G','ss_I','ss_E','ss_B','ss_T','ss_S','ss_L','acc_B','acc_M','acc_E','diso_score','tm8_H','tm8_E','tm8_C','tm8_I','tm8_L','tm8_F','tm8_X','tm8__']  # Replace with your actual column names
    #big_df.columns = column_names

    # Create a DataFrame from the extracted data
    return big_df

In [20]:
for item in clinvar_full['PDB_path'].unique():
    path = item
    protein = str(path).split("/")[-1].split(".")[0]
    if protein in paths:
        raptorx_preds = f'/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/{protein}/{protein}_PROP/{protein}.all'
    else:
        print(f'No RaptorX output for {protein}')
    temp_df = get_ss3(raptorx_preds)
    for index, row in clinvar_full[clinvar_full['PDB_path'] == path].iterrows():
        #print(index)
        # Access the row data using row['column_name'] or row[column_index]
        # modify the row values directly
        # For example, update a specific column value
        pos = clinvar_full['Residue_position'].iloc[index]
        aa = clinvar_full['WT'].iloc[index]
        match = re.search(r'-F(-?\d+)-', protein)
        if match:
            number = int(match.group(1))
            if number == 1:
                retrieve_data(clinvar_full,index,pos,aa)
            else:
                temp_pos = pos-((number-1)*200)
                retrieve_data(clinvar_full,index,temp_pos,aa)
        else:
            print(f"No number found for {protein}.")

In [21]:
clinvar_full

CHR        POS       ID REF ALT   AF_ESP  AF_EXAC AF_TGP ALLELEID  \
0       1  197429459  1048144   G   C      NaN      NaN    NaN  1036051   
1       1  197429466  1213987   T   G      NaN      NaN    NaN  1203980   
2       1  197429467  1963628   G   A      NaN      NaN    NaN  2017299   
3       1  197429468  2202910   G   C      NaN      NaN    NaN  1928560   
4       1  197429473   978993   G   T      NaN      NaN    NaN   967053   
5       1  197429555   191357   G   A      NaN      NaN    NaN   189156   
6       1  197429581   813170   G   C      NaN      NaN    NaN   801275   
7       1  197429587  1017521   T   C      NaN      NaN    NaN  1002377   
8       1  197429605  2093427   G   C      NaN      NaN    NaN  2156507   
9       1  197429614   427863   T   C      NaN      NaN    NaN   418814   
10      1  197434790  1051633   T   C      NaN      NaN    NaN  1039684   
11      1  197434877   846589   A   T      NaN    1e-05    NaN   823132   
12      1  197434880  2502418   C   A      NaN      NaN    NaN  2543901   
13      1  197434880   236473   C   T      NaN      NaN    NaN   237975   
14      1  197434937   973913   G   A      NaN      NaN    NaN   962214   
15      1  197434984   636016   A   G      NaN    1e-05    NaN   623793   
16      1  197435027   973937   T   A      NaN      NaN    NaN   962217   
17      1  197435029  2144426   G   C      NaN      NaN    NaN  1876330   
18      1  197435084  1319944   T   C      NaN      NaN    NaN  1310192   
19      1  197435171   973925   G   T      NaN      NaN    NaN   962218   
20      1  197435305  1456203   T   C      NaN      NaN    NaN  1458143   
21      1  197435323  2202913   T   A      NaN      NaN    NaN  1928563   
22      1  197435351   845976   G   T      NaN    2e-05    NaN   823134   
23      1  197435356  1067464   T   C      NaN      NaN    NaN  1054778   
24      1  197435358   978994   T   G      NaN      NaN    NaN   967054   
...    ..        ...      ...  ..  ..      ...      ...    ...      ...   
31033   X   38411953   935343   G   C      NaN      NaN    NaN   939590   
31034   X   38411955   623201   T   C      NaN      NaN    NaN   612172   
31035   X   38411956  1708452   C   T      NaN      NaN    NaN  1706750   
31036   X   38421026   870332   G   T      NaN      NaN    NaN   858497   
31037   X   38421032   870333   G   A      NaN      NaN    NaN   858498   
31038   X   38421045   859988   C   G      NaN      NaN    NaN   850038   
31039   X   38421051  2110985   A   T      NaN      NaN    NaN  2167554   
31040   X   38421056  2138547   C   T      NaN      NaN    NaN  1878242   
31041   Y    2787207     9752   G   A      NaN      NaN    NaN    24791   
31042   Y    2787224     9756   T   A      NaN      NaN    NaN    24795   
31043   Y    2787224   470196   T   C      NaN      NaN    NaN   472023   
31044   Y    2787267     9744   C   T      NaN      NaN    NaN    24783   
31045   Y    2787278     9738   A   G      NaN      NaN    NaN    24777   
31046   Y    2787287     9742   T   A      NaN      NaN    NaN    24781   
31047   Y    2787320     9755   C   T      NaN      NaN    NaN    24794   
31048   Y    2787321     9750   C   G      NaN      NaN    NaN    24789   
31049   Y    2787334     9741   G   C      NaN      NaN    NaN    24780   
31050   Y    2787377   393470   C   A      NaN      NaN    NaN   380292   
31051   Y    2787392  1470948   G   T      NaN      NaN    NaN  1395175   
31052   Y    2787401     9746   A   G      NaN      NaN    NaN    24785   
31053   Y    2787408  1177296   C   G      NaN      NaN    NaN  1166601   
31054   Y    2787412     9747   C   T      NaN      NaN    NaN    24786   
31055   Y    2787515   492908   C   A      NaN      NaN    NaN   485861   
31056   Y    2787551     9754   C   T      NaN    9e-05    NaN    24793   
31057   Y    7063898   625467   A   T  0.00123  0.00048    NaN   613772   

                                                   CLNDN CLNDNINCL  \
0                         [Leber_co

In [22]:
clinvar_full.to_pickle('clinvar_full_ss3.pkl')

In [23]:
!pwd

/ibex/scratch/penaguka/VAP/thesis
